# نصب پکیج های مورد نیاز

In [ ]:
!pip install -q tensorflow-recommenders
!pip install -q --upgrade tensorflow-datasets
!pip install -q scann

# ایمپورت کتابخانه ها و توابع مورد نیاز

In [1]:
import os
import pprint
import tempfile

from typing import Dict, Text

import numpy as np
import tensorflow as tf
import tensorflow_datasets as tfds

2022-10-24 08:08:46.396405: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-10-24 08:08:46.396473: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/usr/local/lib/python3.9/dist-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
import tensorflow_recommenders as tfrs
import pandas as pd
import numpy as np
import tensorflow as tf


# اتصال به پایگاه داده و گرفتن دیتا

In [3]:
import pyodbc

conn = pyodbc.connect(
        'DRIVER=ODBC Driver 17 for SQL Server;SERVER=GWH,1433;DATABASE=golestanml_test;UID=GC-Rezaie_ai;PWD=R3z@!e123;')

In [105]:
sql_clause = """SELECT
        dc.CustomerBk,
        f.Order_Date,
        f.Product_Code,
        dc.CityBk,
        dc.AreaBk,
        dc.CustomerTypeBk,
        dc.OfficeBk,
        ci.CityTitle,
        so.Actived,
        dc.LastCustomerClassBk,
        dc.DistPathCode
FROM [DWAI].[Sale].[FactV4] f (NOLOCK)
JOIN [DWAI].[Sale].[DimCustomer] dc ON f.CustomerCode = dc.CustomerBk
JOIN [DWAI].[regional].[DimSaleOffice] so ON dc.OfficeBk = so.SaleOfficeBk
JOIN [DWAI].[regional].[DimCity] ci on ci.CityBK = dc.CityBk
WHERE Order_Date BETWEEN 13980901 AND 14010431
AND f.CustomerCode IN (
            SELECT
                    dc.CustomerBk
            FROM [DWAI].[Sale].[DimCustomer] dc
            WHERE dc.DeactiveDate IS NULL
            AND dc.CustomerBk IN (
                    SELECT CustomerCode
                    FROM [DWAI].[Sale].[FactV4]
                )
)"""

a = pd.read_sql(sql_clause, conn)

/usr/local/lib/python3.9/dist-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [106]:
a

CustomerBk  Order_Date  Product_Code  CityBk  AreaBk  CustomerTypeBk  \
0         292034224    13980904           819     149       0              37   
1         138443110    13981003           218    1247       0              37   
2         648502511    13981003           218     112       0              37   
3         243091757    13981004           230     108       5              37   
4         648502511    13981003          1511     112       0              37   
...             ...         ...           ...     ...     ...             ...   
9275780   984084201    14001107          2351     292       0              37   
9275781   263000083    14001105           717     542      15              37   
9275782   795104514    14001105           764    1083       0              37   
9275783   511053208    14001105           764     834      10              37   
9275784   795104514    14001105           779    1083       0              37   

         OfficeBk      CityTitle  Actived  LastCustomerClassBk  DistPathCode  
0             995          ايلام     True                  100             1  
1             236         بروجرد     True                  -10             0  
2             154          تهران     True                  300             5  
3             233          اهواز     True                  100             6  
4             154          تهران     True                  300             5  
...           ...            ...      ...                  ...           ...  
9275780       984        ايزدشهر     True                  300             0  
9275781       968           جاسك     True                  100             3  
9275782       795         چابهار     True                  200             0  
9275783       993  آستانه اشرفيه     True                  100             2  
9275784       795         چابهار     True                  200             0  

[9275785 rows x 11 columns]

In [109]:
sql_clause = """SELECT
        dc.CustomerBk,
        f.Order_Date,
        f.Product_Code,
        dc.CityBk,
        dc.AreaBk,
        dc.CustomerTypeBk,
        dc.OfficeBk,
        ci.CityTitle,
        so.Actived,
        dc.LastCustomerClassBk,
        dc.DistPathCode
FROM [DWAI].[Sale].[FactV4] f (NOLOCK)
JOIN [DWAI].[Sale].[DimCustomer] dc ON f.CustomerCode = dc.CustomerBk
JOIN [DWAI].[regional].[DimSaleOffice] so ON dc.OfficeBk = so.SaleOfficeBk
JOIN [DWAI].[regional].[DimCity] ci on ci.CityBK = dc.CityBk
WHERE Order_Date BETWEEN 14010601 AND 14010730
AND f.CustomerCode IN (
            SELECT
                    dc.CustomerBk
            FROM [DWAI].[Sale].[DimCustomer] dc
            WHERE dc.DeactiveDate IS NULL
            AND dc.CustomerBk IN (
                    SELECT CustomerCode
                    FROM [DWAI].[Sale].[FactV4]
                )
)"""

b = pd.read_sql(sql_clause, conn)

/usr/local/lib/python3.9/dist-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [110]:
b

CustomerBk  Order_Date  Product_Code  CityBk  AreaBk  CustomerTypeBk  \
0         983012065    14010607          2972     125       0              37   
1         221012081    14010608          3013     207      10              37   
2         501321463    14010606          3015    1358       0              52   
3         215000305    14010607          2897     363      80              37   
4         139561267    14010609          2899     101       0              14   
...             ...         ...           ...     ...     ...             ...   
5917790   481013577    14010609          2892     513      13              37   
5917791   976092267    14010613          2896    1216       0              26   
5917792   979011842    14010609           230    1461       0              37   
5917793   993082929    14010610           230     750       0              37   
5917794   993083506    14010610           230     750       0              37   

         OfficeBk CityTitle  Actived  LastCustomerClassBk  DistPathCode  
0             983      مشهد     True                  300             0  
1             158    پيشكوه     True                  200            10  
2             166    مريوان     True                  -10             0  
3             279     ميانه     True                   50             4  
4             139       كرج     True                  -10             0  
...           ...       ...      ...                  ...           ...  
5917790       988   مينودشت     True                  100             5  
5917791       320    آبادان     True                  -10             0  
5917792       328    داورزن     True                  200             0  
5917793       993    لنگرود     True                    0             0  
5917794       993    لنگرود     True                  300             0  

[5917795 rows x 11 columns]

# دو برابر کردن دیتای 6 ماه اخیر

In [8]:
c=pd.concat([b, b])

# تجمیع دیتای دوبرابر شده 6 ماه قبل و داده های قبلی تا 3 سال قبل به میزان یک برابر

In [9]:
df=pd.concat([a, c])

In [10]:
df

CustomerBk  Order_Date  Product_Code  CityBk  AreaBk  CustomerTypeBk  \
0         202001942    14000324           378     292      20              37   
1         315000103    14000324           230     125     100              37   
2         956560666    14000329          1772     112       0              37   
3         956560666    14000329          2351     112       0              37   
4         261302154    14000420          2896     109       0              37   
...             ...         ...           ...     ...     ...             ...   
7851263   201082634    14010720          2785     493       0              52   
7851264   956560481    14010717          2843     118       0              37   
7851265   191000277    14010721          2845     162       9              37   
7851266   191000277    14010721          2853     162       9              37   
7851267   147562269    14010716          2101     112       0              37   

         OfficeBk   CityTitle  Actived  LastCustomerClassBk  DistPathCode  
0             984     ايزدشهر     True                   50             2  
1             983        مشهد     True                  250             1  
2             956       تهران     True                  -10             0  
3             956       تهران     True                  -10             0  
4             968    بندرعباس     True                  200             0  
...           ...         ...      ...                  ...           ...  
7851263       985  فريدونكنار     True                   50             3  
7851264       150       سمنان     True                    0             0  
7851265       138        ساوه     True                  200             1  
7851266       138        ساوه     True                  200             1  
7851267       147       تهران     True                  300             0  

[19402157 rows x 11 columns]

In [11]:
df1=df.reset_index()

In [12]:
df=df1

In [13]:
df.to_csv('first1.csv',index=False)

In [14]:
df = pd.read_csv('first1.csv')

In [15]:
df

index  CustomerBk  Order_Date  Product_Code  CityBk  AreaBk  \
0               0   202001942    14000324           378     292      20   
1               1   315000103    14000324           230     125     100   
2               2   956560666    14000329          1772     112       0   
3               3   956560666    14000329          2351     112       0   
4               4   261302154    14000420          2896     109       0   
...           ...         ...         ...           ...     ...     ...   
19402152  7851263   201082634    14010720          2785     493       0   
19402153  7851264   956560481    14010717          2843     118       0   
19402154  7851265   191000277    14010721          2845     162       9   
19402155  7851266   191000277    14010721          2853     162       9   
19402156  7851267   147562269    14010716          2101     112       0   

          CustomerTypeBk  OfficeBk   CityTitle  Actived  LastCustomerClassBk  \
0                     37       984     ايزدشهر     True                   50   
1                     37       983        مشهد     True                  250   
2                     37       956       تهران     True                  -10   
3                     37       956       تهران     True                  -10   
4                     37       968    بندرعباس     True                  200   
...                  ...       ...         ...      ...                  ...   
19402152              52       985  فريدونكنار     True                   50   
19402153              37       150       سمنان     True                    0   
19402154              37       138        ساوه     True                  200   
19402155              37       138        ساوه     True                  200   
19402156              37       147       تهران     True                  300   

          DistPathCode  
0                    2  
1                    1  
2                    0  
3                    0  
4                    0  
...                ...  
19402152             3  
19402153             0  
19402154             1  
19402155             1  
19402156             0  

[19402157 rows x 12 columns]

In [16]:
df=df[['CustomerBk','CustomerTypeBk','Product_Code','AreaBk','CityTitle','OfficeBk','DistPathCode','LastCustomerClassBk']]

In [17]:
len(df)

19402157

In [18]:
set(df['OfficeBk'][df['CityTitle']=='تبريز'])

{100, 120, 125, 133, 179, 180, 270, 279, 280, 327, 345, 346}

In [19]:
len(set(list(df['OfficeBk'][df['CityTitle']=='تبريز'])+list(df['OfficeBk'][df['CityTitle']=='تهران'])+list(df['OfficeBk'][df['CityTitle']=='اصفهان'])+list(df['OfficeBk'][df['CityTitle']=='مشهد'])))

59

In [20]:
aaa=list(set(list(df['OfficeBk'][df['CityTitle']=='تبريز'])+list(df['OfficeBk'][df['CityTitle']=='تهران'])+list(df['OfficeBk'][df['CityTitle']=='اصفهان'])+list(df['OfficeBk'][df['CityTitle']=='مشهد'])+list(df['OfficeBk'][df['CityTitle']=='شيراز'])+list(df['OfficeBk'][df['CityTitle']=='يزد'])+list(df['OfficeBk'][df['CityTitle']=='اراک'])+list(df['OfficeBk'][df['CityTitle']=='اهواز'])+list(df['OfficeBk'][df['CityTitle']=='رشت'])))

In [21]:
len(aaa)

75

In [22]:
aaa

[129,
 260,
 133,
 902,
 134,
 132,
 138,
 267,
 268,
 139,
 270,
 269,
 272,
 145,
 146,
 147,
 148,
 149,
 150,
 279,
 280,
 275,
 154,
 155,
 156,
 276,
 278,
 159,
 158,
 289,
 157,
 936,
 301,
 176,
 179,
 180,
 948,
 956,
 189,
 959,
 320,
 324,
 325,
 326,
 327,
 200,
 329,
 971,
 975,
 336,
 977,
 210,
 339,
 976,
 982,
 983,
 345,
 346,
 601,
 220,
 273,
 224,
 100,
 122,
 999,
 230,
 233,
 234,
 998,
 237,
 120,
 121,
 250,
 124,
 125]

In [12]:
# len(set(list(df['OfficeBk'][df['CityTitle']=='تهران'])))

In [13]:
# set(list(df['OfficeBk'][df['CityTitle']=='تهران']))

# تفکیک دیتای کلانشهرها از غیر کلانشهرها

In [23]:
lll=[]
lll1 = []
for i in range(len(df)):
    if df['OfficeBk'][i] in aaa:
        lll.append(i)  
    else:
        lll1.append(i)

In [24]:
len(df)

19402157

In [25]:
len(lll)

9436519

In [26]:
len(lll1)

9965638

# ادامه با دیتای کلانشهرها

In [27]:
df2=df.iloc[lll]

In [28]:
df3=df2.reset_index()

In [29]:
df4=df3.iloc[:,1:]

In [30]:
df4

CustomerBk  CustomerTypeBk  Product_Code  AreaBk CityTitle  OfficeBk  \
0         315000103              37           230     100      مشهد       983   
1         956560666              37          1772       0     تهران       956   
2         956560666              37          2351       0     تهران       956   
3         242091574              37          3013      15     اهواز       234   
4         308002495              38           218      16      مشهد       982   
...             ...             ...           ...     ...       ...       ...   
9436514   143561055              37          2521       0     تهران       147   
9436515   956560481              37          2843       0     سمنان       150   
9436516   191000277              37          2845       9      ساوه       138   
9436517   191000277              37          2853       9      ساوه       138   
9436518   147562269              37          2101       0     تهران       147   

         DistPathCode  LastCustomerClassBk  
0                   1                  250  
1                   0                  -10  
2                   0                  -10  
3                   7                  100  
4                   3                  100  
...               ...                  ...  
9436514             0                  200  
9436515             0                    0  
9436516             1                  200  
9436517             1                  200  
9436518             0                  300  

[9436519 rows x 8 columns]

In [31]:
df = df4

In [32]:

df=df.dropna(axis=0, subset=['OfficeBk'])

In [33]:
df = df.reset_index()

In [34]:
df=df.iloc[:,1:]

In [35]:
len(df)

9436519

In [45]:
sql_clause = """/****** Script for SelectTopNRows command from SSMS  ******/
SELECT [ProductSk]
      ,[ProductBK]
      ,[ProductTitle]
      ,[PartUnitName]
      ,[PartUnitweight]
      ,[WholeUnitName]
      ,[WholeUnitContainName]
      ,[WholeUnitCabuture]
      ,[WholeUnitPartUnitRatio]
      ,[Actived]
      ,[RegisteredDate]
      ,[CreatedDate]
      ,[ProductSubGroupBK]
      ,[ProductBrandBK]
  FROM [DWAI].[Inventory].[DimProduct]
  where Actived=1"""

product = pd.read_sql(sql_clause, conn)

/usr/local/lib/python3.9/dist-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [40]:
product.to_csv('product.csv',index=False)

NameError: name 'product' is not defined

# خواندن لیست محولات فعال

In [36]:
df1=pd.read_csv('product.csv')

In [37]:
f=df1['ProductBK'].unique()

In [38]:
f=list(f)

In [39]:
len(f)

544

# استخراج تراکنشهایی که در آنها محصول فعالی خریداری شده

In [40]:
f1=[]
for i in range(len(df)):
    if df['Product_Code'][i] in f:
        f1.append(i)

In [41]:
len(df)

9436519

In [42]:
len(f1)

9425077

In [43]:
df2=df.iloc[f1]

In [44]:
df3=df2.reset_index()

In [45]:
df4=df3.iloc[:,1:]

In [46]:
df4

CustomerBk  CustomerTypeBk  Product_Code  AreaBk CityTitle  OfficeBk  \
0         315000103              37           230     100      مشهد       983   
1         956560666              37          1772       0     تهران       956   
2         956560666              37          2351       0     تهران       956   
3         242091574              37          3013      15     اهواز       234   
4         308002495              38           218      16      مشهد       982   
...             ...             ...           ...     ...       ...       ...   
9425072   143561055              37          2521       0     تهران       147   
9425073   956560481              37          2843       0     سمنان       150   
9425074   191000277              37          2845       9      ساوه       138   
9425075   191000277              37          2853       9      ساوه       138   
9425076   147562269              37          2101       0     تهران       147   

         DistPathCode  LastCustomerClassBk  
0                   1                  250  
1                   0                  -10  
2                   0                  -10  
3                   7                  100  
4                   3                  100  
...               ...                  ...  
9425072             0                  200  
9425073             0                    0  
9425074             1                  200  
9425075             1                  200  
9425076             0                  300  

[9425077 rows x 8 columns]

In [47]:
df = df4

In [48]:
df['CityTitle'].value_counts()

تهران     3352557
مشهد       979797
رشت        426716
اصفهان     364096
شيراز      363295
           ...   
زرند            3
انگوت           3
كندرود          2
كركج            2
هوراند          2
Name: CityTitle, Length: 464, dtype: int64

In [49]:
df['DistPathCode'] = df['DistPathCode'].astype(str)

In [50]:
df['OfficeBk'] = df['OfficeBk'].astype(str)

In [51]:
df['LastCustomerClassBk'] = df['LastCustomerClassBk'].astype(str)

In [52]:
df['CustomerBk'] = df['CustomerBk'].astype(str)

In [53]:
df['CustomerTypeBk'] = df['CustomerTypeBk'].astype(str)

In [54]:
df['AreaBk'] = df['AreaBk'].astype(str)

In [55]:
df['Product_Code'] = df['Product_Code'].astype(str)

In [56]:
df['CityTitle'] = df['CityTitle'].astype(str)

In [58]:
features = ['CustomerBk','AreaBk', 'Product_Code','DistPathCode','CustomerTypeBk','CityTitle','OfficeBk','LastCustomerClassBk'] 
dataset = (
    tf.data.Dataset.from_tensor_slices(
        (
            tf.cast(df[features].values, tf.string)
            
        )
    )
)

In [59]:
dataset

<TensorSliceDataset element_spec=TensorSpec(shape=(8,), dtype=tf.string, name=None)>

In [60]:
import tempfile
ratings = (dataset
           .map(lambda rating: {'user_id': rating[0],'Area_Code':rating[1],'product_title': rating[2],'SalesDocumentType':rating[3],'Customer_Type':rating[4],'city_name':rating[5],'OfficeBk':rating[6],'ClassBk':rating[7]})
           .cache(tempfile.NamedTemporaryFile().name)
)

In [61]:
df

CustomerBk CustomerTypeBk Product_Code AreaBk CityTitle OfficeBk  \
0        315000103             37          230    100      مشهد      983   
1        956560666             37         1772      0     تهران      956   
2        956560666             37         2351      0     تهران      956   
3        242091574             37         3013     15     اهواز      234   
4        308002495             38          218     16      مشهد      982   
...            ...            ...          ...    ...       ...      ...   
9425072  143561055             37         2521      0     تهران      147   
9425073  956560481             37         2843      0     سمنان      150   
9425074  191000277             37         2845      9      ساوه      138   
9425075  191000277             37         2853      9      ساوه      138   
9425076  147562269             37         2101      0     تهران      147   

        DistPathCode LastCustomerClassBk  
0                  1                 250  
1                  0                 -10  
2                  0                 -10  
3                  7                 100  
4                  3                 100  
...              ...                 ...  
9425072            0                 200  
9425073            0                   0  
9425074            1                 200  
9425075            1                 200  
9425076            0                 300  

[9425077 rows x 8 columns]

In [52]:
# dataset=[]

In [53]:
# features = ['CustomerCode', 'Product_Code'] 
# dataset = (
#     tf.data.Dataset.from_tensor_slices(
#         (
#             tf.cast(df[features].values, tf.string)
            
#         )
#     )
# )

In [62]:
dataset

<TensorSliceDataset element_spec=TensorSpec(shape=(8,), dtype=tf.string, name=None)>

In [55]:
# ratings = (dataset
#            .map(lambda rating: {'user_id': rating[0],'product_title':rating[1]})
#            .cache(tempfile.NamedTemporaryFile().name)
# )

In [63]:
ratings

<CacheDataset element_spec={'user_id': TensorSpec(shape=(), dtype=tf.string, name=None), 'Area_Code': TensorSpec(shape=(), dtype=tf.string, name=None), 'product_title': TensorSpec(shape=(), dtype=tf.string, name=None), 'SalesDocumentType': TensorSpec(shape=(), dtype=tf.string, name=None), 'Customer_Type': TensorSpec(shape=(), dtype=tf.string, name=None), 'city_name': TensorSpec(shape=(), dtype=tf.string, name=None), 'OfficeBk': TensorSpec(shape=(), dtype=tf.string, name=None), 'ClassBk': TensorSpec(shape=(), dtype=tf.string, name=None)}>

In [69]:
a = list(df['Product_Code'].unique())
len(a)

542

In [70]:
b = 542*[1]

In [71]:
z=pd.DataFrame({'one':a, 'two':b})

In [72]:
z

one  two
0     230    1
1    1772    1
2    2351    1
3    3013    1
4     218    1
..    ...  ...
537  1678    1
538   360    1
539  1812    1
540  1905    1
541  1058    1

[542 rows x 2 columns]

In [73]:
features = ['one'] 
dataset1 = (
    tf.data.Dataset.from_tensor_slices(
        (
            tf.cast(z[features].values, tf.string)
        )
    )
)

In [74]:
products = (dataset1
          .map(lambda x: x[0])
          .cache(tempfile.NamedTemporaryFile().name))

In [75]:
number_df = len(df)

In [76]:
tf.random.set_seed(42)
shuffled = ratings.shuffle(number_df , seed=42, reshuffle_each_iteration=False)

train = shuffled.take(number_df)
test = shuffled.skip(number_df).take(1)

In [77]:
products

<CacheDataset element_spec=TensorSpec(shape=(), dtype=tf.string, name=None)>

In [78]:
df

CustomerBk CustomerTypeBk Product_Code AreaBk CityTitle OfficeBk  \
0        315000103             37          230    100      مشهد      983   
1        956560666             37         1772      0     تهران      956   
2        956560666             37         2351      0     تهران      956   
3        242091574             37         3013     15     اهواز      234   
4        308002495             38          218     16      مشهد      982   
...            ...            ...          ...    ...       ...      ...   
9425072  143561055             37         2521      0     تهران      147   
9425073  956560481             37         2843      0     سمنان      150   
9425074  191000277             37         2845      9      ساوه      138   
9425075  191000277             37         2853      9      ساوه      138   
9425076  147562269             37         2101      0     تهران      147   

        DistPathCode LastCustomerClassBk  
0                  1                 250  
1                  0                 -10  
2                  0                 -10  
3                  7                 100  
4                  3                 100  
...              ...                 ...  
9425072            0                 200  
9425073            0                   0  
9425074            1                 200  
9425075            1                 200  
9425076            0                 300  

[9425077 rows x 8 columns]

In [67]:
# l11

In [68]:
# user_area

In [79]:
product_title = products.batch(1_000)
user_ids = ratings.batch(10_000_000).map(lambda x: x["user_id"])
user_area = ratings.batch(10_000_000).map(lambda x: x["Area_Code"])
user_sale = ratings.batch(10_000_000).map(lambda x: x["SalesDocumentType"])
user_types = ratings.batch(10_000_000).map(lambda x: x["Customer_Type"])
user_city = ratings.batch(10_000_000).map(lambda x: x["city_name"])
user_city1 = ratings.batch(10_000_000).map(lambda x: x["OfficeBk"])
user_city2 = ratings.batch(10_000_000).map(lambda x: x["ClassBk"])

unique_product_title = np.unique(np.concatenate(list(product_title)))
unique_user_ids = np.unique(np.concatenate(list(user_ids)))
unique_user_area = np.unique(np.concatenate(list(user_area)))
unique_user_sale = np.unique(np.concatenate(list(user_sale)))
unique_user_types = np.unique(np.concatenate(list(user_types)))
unique_user_city = np.unique(np.concatenate(list(user_city)))
unique_user_city1 = np.unique(np.concatenate(list(user_city1)))
unique_user_city2 = np.unique(np.concatenate(list(user_city2)))

unique_product_title[:20]

2022-10-24 08:20:20.993225: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.
2022-10-24 08:25:16.682665: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


array([b'1046', b'1047', b'1048', b'1053', b'1054', b'1055', b'1058',
       b'1059', b'1062', b'1063', b'1070', b'1071', b'1074', b'1075',
       b'1076', b'1077', b'1080', b'1081', b'1086', b'1087'], dtype=object)

In [80]:
unique_product_title

array([b'1046', b'1047', b'1048', b'1053', b'1054', b'1055', b'1058',
       b'1059', b'1062', b'1063', b'1070', b'1071', b'1074', b'1075',
       b'1076', b'1077', b'1080', b'1081', b'1086', b'1087', b'1093',
       b'1094', b'1096', b'1097', b'1098', b'1099', b'1272', b'1274',
       b'1280', b'1282', b'1288', b'1298', b'134', b'137', b'138', b'139',
       b'1408', b'1434', b'1435', b'1436', b'1437', b'1438', b'1439',
       b'1440', b'1443', b'1444', b'1445', b'1448', b'1449', b'1452',
       b'1453', b'1454', b'1455', b'1456', b'1457', b'1458', b'1461',
       b'1462', b'1463', b'1464', b'1465', b'1466', b'1467', b'1469',
       b'147', b'1470', b'1473', b'1474', b'1476', b'1478', b'148',
       b'1484', b'1485', b'1498', b'1511', b'1512', b'1521', b'1522',
       b'1523', b'1524', b'1532', b'1533', b'1541', b'1542', b'1551',
       b'1568', b'1571', b'1572', b'1573', b'1575', b'1576', b'1577',
       b'1578', b'1579', b'1582', b'1583', b'1585', b'1586', b'1587',
       b'1588', b

In [71]:
# product_title = products.batch(1_000)
# user_ids = ratings.batch(1_000_000).map(lambda x: x["user_id"])


# unique_product_title = np.unique(np.concatenate(list(product_title)))
# unique_user_ids = np.unique(np.concatenate(list(user_ids)))


# unique_product_title[:20]

In [81]:
len(unique_product_title)

542

In [82]:
unique_user_ids

array([b'100000003', b'100000101', b'100000252', ..., b'999562014',
       b'999562059', b'999562061'], dtype=object)

In [83]:
unique_product_title

array([b'1046', b'1047', b'1048', b'1053', b'1054', b'1055', b'1058',
       b'1059', b'1062', b'1063', b'1070', b'1071', b'1074', b'1075',
       b'1076', b'1077', b'1080', b'1081', b'1086', b'1087', b'1093',
       b'1094', b'1096', b'1097', b'1098', b'1099', b'1272', b'1274',
       b'1280', b'1282', b'1288', b'1298', b'134', b'137', b'138', b'139',
       b'1408', b'1434', b'1435', b'1436', b'1437', b'1438', b'1439',
       b'1440', b'1443', b'1444', b'1445', b'1448', b'1449', b'1452',
       b'1453', b'1454', b'1455', b'1456', b'1457', b'1458', b'1461',
       b'1462', b'1463', b'1464', b'1465', b'1466', b'1467', b'1469',
       b'147', b'1470', b'1473', b'1474', b'1476', b'1478', b'148',
       b'1484', b'1485', b'1498', b'1511', b'1512', b'1521', b'1522',
       b'1523', b'1524', b'1532', b'1533', b'1541', b'1542', b'1551',
       b'1568', b'1571', b'1572', b'1573', b'1575', b'1576', b'1577',
       b'1578', b'1579', b'1582', b'1583', b'1585', b'1586', b'1587',
       b'1588', b

In [84]:
embedding_dimension = 320

In [85]:
user_model = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_user_ids, mask_token=None),
  # We add an additional embedding to account for unknown tokens.
  tf.keras.layers.Embedding(len(unique_user_ids) + 1, 30)
])

In [86]:
user_model1 = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_user_area, mask_token=None),
  # We add an additional embedding to account for unknown tokens.
  tf.keras.layers.Embedding(len(unique_user_area) + 1, 30)
])

In [87]:
user_model2 = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_user_sale, mask_token=None),
  # We add an additional embedding to account for unknown tokens.
  tf.keras.layers.Embedding(len(unique_user_sale) + 1, 30)
])

In [88]:
user_model3 = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_user_types, mask_token=None),
  # We add an additional embedding to account for unknown tokens.
  tf.keras.layers.Embedding(len(unique_user_types) + 1, 30)
])

In [89]:
user_model4 = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_user_city, mask_token=None),
  # We add an additional embedding to account for unknown tokens.
  tf.keras.layers.Embedding(len(unique_user_city) + 1, 30)
])

In [90]:
user_model5 = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_user_city1, mask_token=None),
  # We add an additional embedding to account for unknown tokens.
  tf.keras.layers.Embedding(len(unique_user_city1) + 1, 30)
])

In [91]:
user_model6 = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_user_city2, mask_token=None),
  # We add an additional embedding to account for unknown tokens.
  tf.keras.layers.Embedding(len(unique_user_city2) + 1, 30)
])

In [92]:
len(unique_user_ids)

40928

In [93]:
type(user_model)

keras.engine.sequential.Sequential

In [94]:
product_model = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_product_title, mask_token=None),
  tf.keras.layers.Embedding(len(unique_product_title) + 1, 210)
])

In [95]:
metrics = tfrs.metrics.FactorizedTopK(
  candidates=products.batch(128).map(product_model)
)

In [96]:
retrieval_task_layer = tfrs.tasks.Retrieval(
  metrics=metrics
)

In [88]:
# class MovielensModel(tfrs.models.Model):

#   def __init__(self, rating_weight: float, retrieval_weight: float) -> None:
#     # We take the loss weights in the constructor: this allows us to instantiate
#     # several model objects with different loss weights.

#     super().__init__()

#     embedding_dimension = 32

#     # User and movie models.
#     self.movie_model: tf.keras.Model = movie_model
#     self.user_model: tf.keras.Model = user_model
#     self.user_model1: tf.keras.Model = user_model1
    
#     # A small model to take in user and movie embeddings and predict ratings.
#     # We can make this as complicated as we want as long as we output a scalar
#     # as our prediction.
#     self.rating_model = tf.keras.Sequential([
#         tf.keras.layers.Dense(256, activation="relu"),
#         tf.keras.layers.Dense(128, activation="relu"),
#         tf.keras.layers.Dense(1),
#     ])

#     # The tasks.

#     self.rating_task: tf.keras.layers.Layer = task
#     self.retrieval_task: tf.keras.layers.Layer = tfrs.tasks.Retrieval(
#         metrics=tfrs.metrics.FactorizedTopK(
#             candidates=movies.batch(128).map(self.movie_model)
#         )
#     )

#     # The loss weights.


#   def call(self, features: Dict[Text, tf.Tensor]) -> tf.Tensor:
#     # We pick out the user features and pass them into the user model.
#     user_embeddings = self.user_model(features["user_id"])
#     user_embeddings1 = self.user_model1(features["Customer_Type"])
#     # And pick out the movie features and pass them into the movie model.
#     movie_embeddings = self.movie_model(features["movie_title"])
    
#     return (
#         user_embeddings,
#         user_embeddings1,
#         # We apply the multi-layered rating model to a concatentation of
#         # user and movie embeddings.
#         self.rating_model(
#             tf.concat([user_embeddings, user_embeddings1], axis=1)
#         ),
#     )

#   def compute_loss(self, features: Dict[Text, tf.Tensor], training=False) -> tf.Tensor:

#     ratings = features.pop("user_rating")

#     user_embeddings, movie_embeddings, rating_predictions = self(features)

#     # We compute the loss for each task.
#     rating_loss = self.rating_task(
#         labels=ratings,
#         predictions=rating_predictions,
#     )
#     retrieval_loss = self.retrieval_task(user_embeddings, movie_embeddings)

#     # And combine them using the loss weights.
#     return (self.rating_weight * rating_loss
#             + self.retrieval_weight * retrieval_loss)

In [97]:
user_model

In [98]:
class productModel(tfrs.models.Model):
  """MovieLens candidate generation model"""
 
  def __init__( self,user_model,user_model1,user_model2,user_model3,user_model4,user_model5,user_model6, product_model,retrieval_task_layer):
    
    super().__init__()
    self.product_model: tf.keras.Model = product_model
    self.user_model: tf.keras.Model = user_model
    self.user_model1: tf.keras.Model = user_model1
    self.user_model2: tf.keras.Model = user_model2
    self.user_model3: tf.keras.Model = user_model3
    self.user_model4: tf.keras.Model = user_model4
    self.user_model5: tf.keras.Model = user_model5
    self.user_model6: tf.keras.Model = user_model6
    self.retrieval_task_layer: tf.keras.layers.Layer = retrieval_task_layer


    
    # #self.query_embeddings_ds_1 = tf.keras.layers.Dense(128, activation='relu')
    # self.query_embeddings_ds_2 = tf.keras.layers.Dense(64, activation='relu')
    # self.query_embeddings_ds_3 = tf.keras.layers.Dense(32, activation='relu')
    
    # self.positive_candidate_embeddings_ds_1 = tf.keras.layers.Dense(128, activation='relu')
    # self.positive_candidate_embeddings_ds_2 = tf.keras.layers.Dense(64, activation='relu')
    # self.positive_candidate_embeddings_ds_3 = tf.keras.layers.Dense(32, activation='relu')
    
    # self.prd_sls_dff_reshape = tf.keras.layers.Reshape([1])#keras.layers.Reshape((None,1))
    # self.cst_sls_dff_reshape = tf.keras.layers.Reshape([1])#keras.layers.Reshape((None,1))
    # self.int_q_su_reshape = tf.keras.layers.Reshape([1])#keras.layers.Reshape((None,1))
    # self.prv_int_q_su_reshape = tf.keras.layers.Reshape([1])#keras.layers.Reshape((None,1))
    
 
 #def compute_loss(self, features: Dict[Text, tf.Tensor], training=False):
  def compute_loss(self, features, training=False) -> tf.Tensor:
    
    print(features)
    user_embeddings = self.user_model(features["user_id"])
    user_embeddings1 = self.user_model1(features["Area_Code"])
    user_embeddings2 = self.user_model2(features["SalesDocumentType"])
    user_embeddings3 = self.user_model3(features["Customer_Type"])
    user_embeddings4 = self.user_model4(features["city_name"])
    user_embeddings5 = self.user_model5(features["OfficeBk"])
    user_embeddings6 = self.user_model6(features["ClassBk"])
    product_embeddings = self.product_model(features["product_title"])
    
    query_embeddings_concats = tf.concat([user_embeddings, user_embeddings1,user_embeddings2,user_embeddings3,user_embeddings4,user_embeddings5,user_embeddings6], axis=1)
    
#     query_embeddings_final = self.query_embeddings_ds_3(
#         self.query_embeddings_ds_2(
#             self.query_embeddings_ds_1(
#                 query_embeddings_concats
#             )
#         )
#     )
    
    query_embeddings_final = query_embeddings_concats
    
    
    #t2 = self.res(self.raw_user_age_normalization_layer(features["raw_user_age"]))
    
    positive_candidate_embeddings_concats = product_embeddings
    
    positive_candidate_embeddings_final = positive_candidate_embeddings_concats

#     print(query_embeddings)
#     print(positive_candidate_embeddings)

    loss = self.retrieval_task_layer(
        query_embeddings_final,
        positive_candidate_embeddings_final
        # ,compute_metrics=not training  # To speed up training
    )
    return loss

In [91]:
# class MovielensModel(tfrs.Model):

#   def __init__(self, user_model, movie_model):
#     super().__init__()
#     self.movie_model: tf.keras.Model = movie_model
#     self.user_model: tf.keras.Model = user_model
#     self.task: tf.keras.layers.Layer = task

#   def compute_loss(self, features: Dict[Text, tf.Tensor], training=False) -> tf.Tensor:
#     # We pick out the user features and pass them into the user model.
#     user_embeddings = self.user_model(features["user_id"])
#     # And pick out the movie features and pass them into the movie model,
#     # getting embeddings back.
#     positive_movie_embeddings = self.movie_model(features["movie_title"])

#     # The task computes the loss and the metrics.
#     return self.task(user_embeddings, positive_movie_embeddings)

In [92]:
# class NoBaseClassMovielensModel(tf.keras.Model):

#   def __init__(self, user_model, movie_model):
#     super().__init__()
#     self.movie_model: tf.keras.Model = movie_model
#     self.user_model: tf.keras.Model = user_model
#     self.task: tf.keras.layers.Layer = task

#   def train_step(self, features: Dict[Text, tf.Tensor]) -> tf.Tensor:

#     # Set up a gradient tape to record gradients.
#     with tf.GradientTape() as tape:

#       # Loss computation.
#       user_embeddings = self.user_model(features["user_id"])
#       positive_movie_embeddings = self.movie_model(features["movie_title"])
#       loss = self.task(user_embeddings, positive_movie_embeddings)

#       # Handle regularization losses as well.
#       regularization_loss = sum(self.losses)

#       total_loss = loss + regularization_loss

#     gradients = tape.gradient(total_loss, self.trainable_variables)
#     self.optimizer.apply_gradients(zip(gradients, self.trainable_variables))

#     metrics = {metric.name: metric.result() for metric in self.metrics}
#     metrics["loss"] = loss
#     metrics["regularization_loss"] = regularization_loss
#     metrics["total_loss"] = total_loss

#     return metrics

#   def test_step(self, features: Dict[Text, tf.Tensor]) -> tf.Tensor:

#     # Loss computation.
#     user_embeddings = self.user_model(features["user_id"])
#     positive_movie_embeddings = self.movie_model(features["movie_title"])
#     loss = self.task(user_embeddings, positive_movie_embeddings)

#     # Handle regularization losses as well.
#     regularization_loss = sum(self.losses)

#     total_loss = loss + regularization_loss

#     metrics = {metric.name: metric.result() for metric in self.metrics}
#     metrics["loss"] = loss
#     metrics["regularization_loss"] = regularization_loss
#     metrics["total_loss"] = total_loss

#     return metrics

In [93]:
# class MovielensModel(tfrs.models.Model):
#   """MovieLens candidate generation model"""
 
#   def __init__( self,user_model,product_model,retrieval_task_layer):
    
#     super().__init__()
#     self.product_model: tf.keras.Model = product_model
#     self.user_model: tf.keras.Model = user_model
#     # self.user_model1: tf.keras.Model = user_model1
#     # self.user_model2: tf.keras.Model = user_model2
#     # self.user_model3: tf.keras.Model = user_model3
#     # self.user_model4: tf.keras.Model = user_model4
#     self.retrieval_task_layer: tf.keras.layers.Layer = retrieval_task_layer


    
#     # #self.query_embeddings_ds_1 = tf.keras.layers.Dense(128, activation='relu')
#     # self.query_embeddings_ds_2 = tf.keras.layers.Dense(64, activation='relu')
#     # self.query_embeddings_ds_3 = tf.keras.layers.Dense(32, activation='relu')
    
#     # self.positive_candidate_embeddings_ds_1 = tf.keras.layers.Dense(128, activation='relu')
#     # self.positive_candidate_embeddings_ds_2 = tf.keras.layers.Dense(64, activation='relu')
#     # self.positive_candidate_embeddings_ds_3 = tf.keras.layers.Dense(32, activation='relu')
    
#     # self.prd_sls_dff_reshape = tf.keras.layers.Reshape([1])#keras.layers.Reshape((None,1))
#     # self.cst_sls_dff_reshape = tf.keras.layers.Reshape([1])#keras.layers.Reshape((None,1))
#     # self.int_q_su_reshape = tf.keras.layers.Reshape([1])#keras.layers.Reshape((None,1))
#     # self.prv_int_q_su_reshape = tf.keras.layers.Reshape([1])#keras.layers.Reshape((None,1))
    
 
#  #def compute_loss(self, features: Dict[Text, tf.Tensor], training=False):
#   def compute_loss(self, features, training=False) -> tf.Tensor:
    
#     print(features)
#     user_embeddings = self.user_model(features["user_id"])

#     product_embeddings = self.product_model(features["product_title"])
    
#     query_embeddings_concats = user_embeddings
    
# #     query_embeddings_final = self.query_embeddings_ds_3(
# #         self.query_embeddings_ds_2(
# #             self.query_embeddings_ds_1(
# #                 query_embeddings_concats
# #             )
# #         )
# #     )
    
#     query_embeddings_final = query_embeddings_concats
    
    
#     #t2 = self.res(self.raw_user_age_normalization_layer(features["raw_user_age"]))
    
#     positive_candidate_embeddings_concats = product_embeddings
    
#     positive_candidate_embeddings_final = positive_candidate_embeddings_concats

# #     print(query_embeddings)
# #     print(positive_candidate_embeddings)

#     loss = self.retrieval_task_layer(
#         query_embeddings_final,
#         positive_candidate_embeddings_final
#         # ,compute_metrics=not training  # To speed up training
#     )
#     return loss

In [99]:
len(df)

9425077

In [100]:
model = productModel(user_model,user_model1,user_model2,user_model3,user_model4,user_model5,user_model6, product_model,retrieval_task_layer)
model.compile(optimizer=tf.keras.optimizers.Adagrad(learning_rate=0.1))

In [97]:
# model = MovielensModel(user_model, product_model,retrieval_task_layer)
# model.compile(optimizer=tf.keras.optimizers.Adagrad(learning_rate=0.1))

In [101]:
cached_train = train.shuffle(9380118).batch(8192).cache()
cached_test = test.batch(4096).cache()

In [102]:
model.fit(cached_train, epochs=7)

Epoch 1/7
{'user_id': <tf.Tensor 'IteratorGetNext:7' shape=(None,) dtype=string>, 'Area_Code': <tf.Tensor 'IteratorGetNext:0' shape=(None,) dtype=string>, 'product_title': <tf.Tensor 'IteratorGetNext:6' shape=(None,) dtype=string>, 'SalesDocumentType': <tf.Tensor 'IteratorGetNext:4' shape=(None,) dtype=string>, 'Customer_Type': <tf.Tensor 'IteratorGetNext:2' shape=(None,) dtype=string>, 'city_name': <tf.Tensor 'IteratorGetNext:5' shape=(None,) dtype=string>, 'OfficeBk': <tf.Tensor 'IteratorGetNext:3' shape=(None,) dtype=string>, 'ClassBk': <tf.Tensor 'IteratorGetNext:1' shape=(None,) dtype=string>}
{'user_id': <tf.Tensor 'IteratorGetNext:7' shape=(None,) dtype=string>, 'Area_Code': <tf.Tensor 'IteratorGetNext:0' shape=(None,) dtype=string>, 'product_title': <tf.Tensor 'IteratorGetNext:6' shape=(None,) dtype=string>, 'SalesDocumentType': <tf.Tensor 'IteratorGetNext:4' shape=(None,) dtype=string>, 'Customer_Type': <tf.Tensor 'IteratorGetNext:2' shape=(None,) dtype=string>, 'city_name': <

2022-10-24 08:44:34.118592: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:390] Filling up shuffle buffer (this may take a while): 818528 of 9425077
2022-10-24 08:44:44.118605: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:390] Filling up shuffle buffer (this may take a while): 1643932 of 9425077
2022-10-24 08:44:54.118585: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:390] Filling up shuffle buffer (this may take a while): 2449839 of 9425077
2022-10-24 08:45:04.118585: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:390] Filling up shuffle buffer (this may take a while): 3253268 of 9425077
2022-10-24 08:45:14.118587: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:390] Filling up shuffle buffer (this may take a while): 4052384 of 9425077
2022-10-24 08:45:24.118585: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:390] Filling up shuffle buffer (this may take a while): 4856997 of 9425077
2022-10-24 08:45:34.118593: I tensorflow/core/kernels/data/shuffl

 696/1151 [=================>............] - ETA: 2:56 - factorized_top_k/top_1_categorical_accuracy: 0.0303 - factorized_top_k/top_5_categorical_accuracy: 0.1851 - factorized_top_k/top_10_categorical_accuracy: 0.2983 - factorized_top_k/top_50_categorical_accuracy: 0.6300 - factorized_top_k/top_100_categorical_accuracy: 0.7757 - loss: 64187.0425 - regularization_loss: 0.0000e+00 - total_loss: 64187.0425

KeyboardInterrupt: 

# خواندن لیست مشتریانی که تا کنون تراکنش داشته اند به همراه 8 فیچر آنها 

In [101]:
dd = pd.read_csv('customers_with_trans_14010611.csv')

In [102]:
dd

CustomerBk  AreaBk  LastCustomerClassBk  CustomerTypeBk  DistPathCode  \
0       102000008       0                    0              37             0   
1       102000011       0                    0              37             0   
2       102000014       0                    0              37             0   
3       102013362       0                    0              37             0   
4       102013374       0                    0              37             0   
...           ...     ...                  ...             ...           ...   
84665   999562006       0                  200              22             0   
84666   999562007       0                  250              37             0   
84667   999562008       0                  200              39             0   
84668   999562009       0                  300              37             0   
84669   999562010       0                    0              54             0   

       OfficeBk  CityBk CityTitle  Actived  
0           236    1276    كميجان     True  
1           138     104      اراك     True  
2           138     104      اراك     True  
3           138     104      اراك     True  
4           138     104      اراك     True  
...         ...     ...       ...      ...  
84665       999     112     تهران     True  
84666       999     112     تهران     True  
84667       999     112     تهران     True  
84668       999     112     تهران     True  
84669       999     112     تهران     True  

[84670 rows x 9 columns]

# خواندن لیست مشتریانی که تا کنون تراکنش نداشته اند به همراه 8 فیچر آنها 

In [103]:
dg = pd.read_csv('customers_no_trans_14010611.csv')

In [104]:
dg

CustomerBk  AreaBk  LastCustomerClassBk  CustomerTypeBk  DistPathCode  \
0               0       0                    0               0             0   
1       102000013       0                    0              37             0   
2       102000015       0                    0              37             0   
3       102013378       0                    0              37             0   
4       102013385       0                    0              37             0   
...           ...     ...                  ...             ...           ...   
18507   997105219       0                    0              37             0   
18508   998442479       0                  -10              26             0   
18509   998442480       0                  -10              22             0   
18510   998442482       0                  -10              22             0   
18511   999562001       0                  -10               9             0   

       OfficeBk  CityBk CityTitle  Actived  
0             0       0    نامشخص    False  
1           138     104      اراك     True  
2           138     104      اراك     True  
3           236    1267     شازند     True  
4           236    1536   ميلاجرد     True  
...         ...     ...       ...      ...  
18507       997     113  خرم آباد     True  
18508       998     108     اهواز     True  
18509       998     108     اهواز     True  
18510       998     108     اهواز     True  
18511       999     112     تهران     True  

[18512 rows x 9 columns]

In [105]:
# len(pd.unique(df['CustomerBk']))

In [106]:
# df1=df.drop_duplicates('CustomerBk', keep='first')

In [107]:
df['CityTitle'][0]

'تهران'

In [108]:
dd=dd[['CustomerBk','CustomerTypeBk','AreaBk','CityTitle','OfficeBk','DistPathCode','LastCustomerClassBk']]

In [109]:
dg=dg[['CustomerBk','CustomerTypeBk','AreaBk','CityTitle','OfficeBk','DistPathCode','LastCustomerClassBk']]

# تجمیع کل مشتریان

In [110]:
dr = pd.concat([dd,dg])

In [111]:
dr

CustomerBk  CustomerTypeBk  AreaBk CityTitle  OfficeBk  DistPathCode  \
0       102000008              37       0    كميجان       236             0   
1       102000011              37       0      اراك       138             0   
2       102000014              37       0      اراك       138             0   
3       102013362              37       0      اراك       138             0   
4       102013374              37       0      اراك       138             0   
...           ...             ...     ...       ...       ...           ...   
18507   997105219              37       0  خرم آباد       997             0   
18508   998442479              26       0     اهواز       998             0   
18509   998442480              22       0     اهواز       998             0   
18510   998442482              22       0     اهواز       998             0   
18511   999562001               9       0     تهران       999             0   

       LastCustomerClassBk  
0                        0  
1                        0  
2                        0  
3                        0  
4                        0  
...                    ...  
18507                    0  
18508                  -10  
18509                  -10  
18510                  -10  
18511                  -10  

[103182 rows x 7 columns]

In [112]:
dr2=dr.reset_index()

In [113]:
dr3=dr2.iloc[:,1:]

In [114]:
# bbb=[156,959,972]

In [115]:
dr3

CustomerBk  CustomerTypeBk  AreaBk CityTitle  OfficeBk  DistPathCode  \
0        102000008              37       0    كميجان       236             0   
1        102000011              37       0      اراك       138             0   
2        102000014              37       0      اراك       138             0   
3        102013362              37       0      اراك       138             0   
4        102013374              37       0      اراك       138             0   
...            ...             ...     ...       ...       ...           ...   
103177   997105219              37       0  خرم آباد       997             0   
103178   998442479              26       0     اهواز       998             0   
103179   998442480              22       0     اهواز       998             0   
103180   998442482              22       0     اهواز       998             0   
103181   999562001               9       0     تهران       999             0   

        LastCustomerClassBk  
0                         0  
1                         0  
2                         0  
3                         0  
4                         0  
...                     ...  
103177                    0  
103178                  -10  
103179                  -10  
103180                  -10  
103181                  -10  

[103182 rows x 7 columns]

In [116]:
# for i in range(len(dr2)):
#     dr2['OfficeBk'][i] = int(dr2['OfficeBk'][i])
    

In [117]:
type(dr2['OfficeBk'][97892])

numpy.int64

In [118]:
aaa

[129,
 260,
 133,
 902,
 134,
 132,
 138,
 267,
 268,
 139,
 272,
 273,
 146,
 147,
 148,
 149,
 150,
 279,
 280,
 154,
 155,
 156,
 157,
 158,
 159,
 289,
 936,
 948,
 950,
 956,
 959,
 320,
 324,
 325,
 326,
 327,
 200,
 329,
 971,
 975,
 336,
 977,
 210,
 339,
 976,
 982,
 983,
 345,
 346,
 220,
 230,
 999,
 998,
 233,
 234,
 237,
 250]

In [119]:
dr2

index  CustomerBk  CustomerTypeBk  AreaBk CityTitle  OfficeBk  \
0           0   102000008              37       0    كميجان       236   
1           1   102000011              37       0      اراك       138   
2           2   102000014              37       0      اراك       138   
3           3   102013362              37       0      اراك       138   
4           4   102013374              37       0      اراك       138   
...       ...         ...             ...     ...       ...       ...   
103177  18507   997105219              37       0  خرم آباد       997   
103178  18508   998442479              26       0     اهواز       998   
103179  18509   998442480              22       0     اهواز       998   
103180  18510   998442482              22       0     اهواز       998   
103181  18511   999562001               9       0     تهران       999   

        DistPathCode  LastCustomerClassBk  
0                  0                    0  
1                  0                    0  
2                  0                    0  
3                  0                    0  
4                  0                    0  
...              ...                  ...  
103177             0                    0  
103178             0                  -10  
103179             0                  -10  
103180             0                  -10  
103181             0                  -10  

[103182 rows x 8 columns]

In [120]:
dr2.to_csv('dr2.csv',index=False)

In [121]:
dr2 = pd.read_csv('dr2.csv')

In [122]:
dr2

index  CustomerBk  CustomerTypeBk  AreaBk CityTitle  OfficeBk  \
0           0   102000008              37       0    كميجان       236   
1           1   102000011              37       0      اراك       138   
2           2   102000014              37       0      اراك       138   
3           3   102013362              37       0      اراك       138   
4           4   102013374              37       0      اراك       138   
...       ...         ...             ...     ...       ...       ...   
103177  18507   997105219              37       0  خرم آباد       997   
103178  18508   998442479              26       0     اهواز       998   
103179  18509   998442480              22       0     اهواز       998   
103180  18510   998442482              22       0     اهواز       998   
103181  18511   999562001               9       0     تهران       999   

        DistPathCode  LastCustomerClassBk  
0                  0                    0  
1                  0                    0  
2                  0                    0  
3                  0                    0  
4                  0                    0  
...              ...                  ...  
103177             0                    0  
103178             0                  -10  
103179             0                  -10  
103180             0                  -10  
103181             0                  -10  

[103182 rows x 8 columns]

# جدا کردن مشتریان کلانشهرها

In [123]:
lll=[]
lll1 = []
for i in range(len(dr2)):
    if dr2['OfficeBk'][i] in aaa:
        lll.append(i)  
    else:
        lll1.append(i)

In [124]:
dr3=dr2.iloc[lll]

In [125]:
dr3=dr3.reset_index()

In [126]:
# dd4=dr3.iloc[:,2:]

In [127]:
# dd4

In [128]:
df = dr3[['CustomerBk','CustomerTypeBk','AreaBk','CityTitle','OfficeBk','DistPathCode','LastCustomerClassBk']]

In [129]:
df

CustomerBk  CustomerTypeBk  AreaBk CityTitle  OfficeBk  DistPathCode  \
0       102000011              37       0      اراك       138             0   
1       102000014              37       0      اراك       138             0   
2       102013362              37       0      اراك       138             0   
3       102013374              37       0      اراك       138             0   
4       102013394              26       0      اراك       138             0   
...           ...             ...     ...       ...       ...           ...   
56175   992084763              37       0       رشت       273             0   
56176   998442479              26       0     اهواز       998             0   
56177   998442480              22       0     اهواز       998             0   
56178   998442482              22       0     اهواز       998             0   
56179   999562001               9       0     تهران       999             0   

       LastCustomerClassBk  
0                        0  
1                        0  
2                        0  
3                        0  
4                        0  
...                    ...  
56175                  -10  
56176                  -10  
56177                  -10  
56178                  -10  
56179                  -10  

[56180 rows x 7 columns]

In [131]:
df['CustomerBk'] = df['CustomerBk'].astype(str)
df['CustomerTypeBk'] = df['CustomerTypeBk'].astype(str)
df['AreaBk'] = df['AreaBk'].astype(str)
df['CityTitle'] = df['CityTitle'].astype(str)
df['OfficeBk'] = df['OfficeBk'].astype(str)
df['DistPathCode'] = df['DistPathCode'].astype(str)
df['LastCustomerClassBk'] = df['LastCustomerClassBk'].astype(str)

/tmp/ipykernel_44/1376161466.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['CustomerBk'] = df['CustomerBk'].astype(str)
/tmp/ipykernel_44/1376161466.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['CustomerTypeBk'] = df['CustomerTypeBk'].astype(str)
/tmp/ipykernel_44/1376161466.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.or

In [132]:
df

CustomerBk CustomerTypeBk AreaBk CityTitle OfficeBk DistPathCode  \
0      102000011             37      0      اراك      138            0   
1      102000014             37      0      اراك      138            0   
2      102013362             37      0      اراك      138            0   
3      102013374             37      0      اراك      138            0   
4      102013394             26      0      اراك      138            0   
...          ...            ...    ...       ...      ...          ...   
56175  992084763             37      0       رشت      273            0   
56176  998442479             26      0     اهواز      998            0   
56177  998442480             22      0     اهواز      998            0   
56178  998442482             22      0     اهواز      998            0   
56179  999562001              9      0     تهران      999            0   

      LastCustomerClassBk  
0                       0  
1                       0  
2                       0  
3                       0  
4                       0  
...                   ...  
56175                 -10  
56176                 -10  
56177                 -10  
56178                 -10  
56179                 -10  

[56180 rows x 7 columns]

In [133]:
df5=df.iloc[:10000,:]

In [134]:
df5=df5.reset_index()

In [135]:
df5=df5.iloc[:,1:]

In [136]:
df5

CustomerBk CustomerTypeBk AreaBk CityTitle OfficeBk DistPathCode  \
0     102000011             37      0      اراك      138            0   
1     102000014             37      0      اراك      138            0   
2     102013362             37      0      اراك      138            0   
3     102013374             37      0      اراك      138            0   
4     102013394             26      0      اراك      138            0   
...         ...            ...    ...       ...      ...          ...   
9995  221011379             37      4   نصرآباد      159            8   
9996  221011383             37     19       يزد      159            7   
9997  221011404             37      5       يزد      158            5   
9998  221011430             37      3       يزد      159            1   
9999  221011431             37      7       يزد      159            3   

     LastCustomerClassBk  
0                      0  
1                      0  
2                      0  
3                      0  
4                      0  
...                  ...  
9995                 100  
9996                 250  
9997                 250  
9998                 250  
9999                 100  

[10000 rows x 7 columns]

In [137]:
features = ['CustomerBk','AreaBk','DistPathCode','CustomerTypeBk','CityTitle','OfficeBk','LastCustomerClassBk'] 
dataset = (
    tf.data.Dataset.from_tensor_slices(
        (
            tf.cast(df5[features].values, tf.string)
            
        )
    )
)

In [138]:
ratings = (dataset
           .map(lambda rating: {'user_id': rating[0],'Area_Code':rating[1],'SalesDocumentType':rating[2],'Customer_Type':rating[3],'city_name':rating[4],'OfficeBk':rating[5],'ClassBk':rating[6]})
           .cache(tempfile.NamedTemporaryFile().name)
)

In [139]:
tf.random.set_seed(42)
shuffled = ratings.shuffle(10000 , seed=42, reshuffle_each_iteration=False)

train = shuffled.take(10000)


In [140]:
l=[]
for i in range(10000):
    l1=[]
    # index = tfrs.layers.factorized_top_k.BruteForce(model.user_model,100)
    # # recommends movies out of the entire movies dataset.
    # index.index_from_dataset(
    #   tf.data.Dataset.zip((products.batch(100), products.batch(100).map(product_model)))
    # )
    brute_force_layer = tfrs.layers.factorized_top_k.BruteForce(k=150)
    brute_force_layer.index_from_dataset(
      tf.data.Dataset.zip((products.batch(100), products.batch(100).map(product_model)))
    )

    cached_test = train.batch(1)

    test_sample = cached_test.skip(i).take(1)
    test_sample_map = test_sample.map(
            lambda features: tf.concat([model.user_model(features["user_id"]), model.user_model1(features["Area_Code"]),model.user_model2(features["SalesDocumentType"]),model.user_model3(features["Customer_Type"]), model.user_model4(features["city_name"]), model.user_model5(features["OfficeBk"]), model.user_model6(features["ClassBk"])], axis=1)
        )

    test_sample_map_arr = []
    for item in test_sample_map.take(1).as_numpy_iterator():
        test_sample_map_arr.append(item[0])
    test_sample_map_arr = np.array(test_sample_map_arr)

    afinity_scores, a = brute_force_layer(test_sample_map_arr)

    for item in test_sample.as_numpy_iterator():
        print(f"Recommendations for user {item['user_id']} using BruteForce: {i}")
        # ppp = 1

    l1.append(int(item['user_id']))
    # Get recommendations.
    # _, titles = index(tf.constant([i]))
    z=list(a[0, :150].numpy())
    for j in z:
        l1.append(int(j))
        
    l.append(l1)

2022-09-27 07:31:41.653991: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


Recommendations for user [b'134442360'] using BruteForce: 0


2022-09-27 07:31:41.878045: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.
2022-09-27 07:31:42.503198: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


Recommendations for user [b'155561306'] using BruteForce: 1
Recommendations for user [b'146561260'] using BruteForce: 2
Recommendations for user [b'144442815'] using BruteForce: 3
Recommendations for user [b'144443404'] using BruteForce: 4
Recommendations for user [b'221010099'] using BruteForce: 5
Recommendations for user [b'149560987'] using BruteForce: 6
Recommendations for user [b'136561198'] using BruteForce: 7
Recommendations for user [b'215000264'] using BruteForce: 8
Recommendations for user [b'158443569'] using BruteForce: 9
Recommendations for user [b'213020218'] using BruteForce: 10
Recommendations for user [b'213030820'] using BruteForce: 11
Recommendations for user [b'114013175'] using BruteForce: 12
Recommendations for user [b'128560808'] using BruteForce: 13
Recommendations for user [b'155561387'] using BruteForce: 14
Recommendations for user [b'158443422'] using BruteForce: 15
Recommendations for user [b'159443580'] using BruteForce: 16
Recommendations for user [b'14800

In [141]:
len(l)

10000

In [142]:
dd1=pd.DataFrame(l)

In [143]:
dd1

0     1     2     3     4     5     6     7     8     9    ...  \
0     134442360  2211   232  2364  2323   239  2112   238   235   277  ...   
1     155561306  2018  2041  2509  1952   819  2761   508   501  1661  ...   
2     146561260  1053  2761  1847  1055   279  2865  3032   457  2363  ...   
3     144442815  1093  2613   221  1099  1070  1094   805   788   371  ...   
4     144443404  2613   221  2610  2629   277   275   276   232   235  ...   
...         ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
9995  158443585  1763  2112  1764  2101  2111  1071  1761   279  1760  ...   
9996  146561482  3116  2865   279  2111  2363   218  1685   207  1857  ...   
9997  138442971  2864   221   589   230  3033   808   591  1280  2468  ...   
9998  148561120  2358  2868  2114  2351  2101   218  2363   207  2364  ...   
9999  219030437   289  3038  3032  3077  2018   147   228  3030   229  ...   

       141   142   143   144   145   146   147   148   149   150  
0     1664  3121   460   291  1685  1062  1532  1648   657  2018  
1     3121   827   496  1449   235   238   137   407  1618  2245  
2     1474  2509  1763  2011  1608   703  3014   325   650  2905  
3     1930  1583   230  1449   370  2905  1077   808   736  1438  
4     2041   420   377   137  1765   375   457   383  2885  3010  
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
9995  1478   365  1646  1807  2020  1808  1606  1588   818   277  
9996  1511  2851  1894  1691  1601  1854  1844  1055   819   291  
9997  1618  2022  3014  2509  1754   757  1571  1099  1648   736  
9998  2853   501  1894  1857  1805  2889  1606   657  2892   276  
9999  1773  2613  1452  2609   238   452  2512  3000  1775  2469  

[10000 rows x 151 columns]

In [144]:
dd1.to_csv('part1.csv')

In [145]:
df5=df.iloc[10000:20000,:]

In [146]:
df5=df5.reset_index()

In [147]:
df5=df5.iloc[:,1:]

In [148]:
df5

CustomerBk CustomerTypeBk AreaBk CityTitle OfficeBk DistPathCode  \
0     221011436             37      6     مهريز      159            8   
1     221011449             37      5    ابركوه      159            6   
2     221011466             37      4       يزد      158            1   
3     221011472             38     19       يزد      159            4   
4     221011528             37     19    اردكان      158            3   
...         ...            ...    ...       ...      ...          ...   
9995  611502480             37      0     تهران      156            2   
9996  611502495             37      0     تهران      156            2   
9997  611502510             37      0     تهران      156            2   
9998  611502516             37      0     تهران      156            1   
9999  611502520             37      0     تهران      156            2   

     LastCustomerClassBk  
0                    100  
1                    200  
2                    300  
3                    300  
4                    250  
...                  ...  
9995                 100  
9996                 100  
9997                 100  
9998                 100  
9999                 100  

[10000 rows x 7 columns]

In [150]:
features = ['CustomerBk','AreaBk','DistPathCode','CustomerTypeBk','CityTitle','OfficeBk','LastCustomerClassBk'] 
dataset = (
    tf.data.Dataset.from_tensor_slices(
        (
            tf.cast(df5[features].values, tf.string)
            
        )
    )
)

In [151]:
ratings = (dataset
           .map(lambda rating: {'user_id': rating[0],'Area_Code':rating[1],'SalesDocumentType':rating[2],'Customer_Type':rating[3],'city_name':rating[4],'OfficeBk':rating[5],'ClassBk':rating[6]})
           .cache(tempfile.NamedTemporaryFile().name)
)

In [152]:
tf.random.set_seed(42)
shuffled = ratings.shuffle(10000 , seed=42, reshuffle_each_iteration=False)

train = shuffled.take(10000)


In [153]:
l=[]
for i in range(10000):
    l1=[]
    # index = tfrs.layers.factorized_top_k.BruteForce(model.user_model,100)
    # # recommends movies out of the entire movies dataset.
    # index.index_from_dataset(
    #   tf.data.Dataset.zip((products.batch(100), products.batch(100).map(product_model)))
    # )
    brute_force_layer = tfrs.layers.factorized_top_k.BruteForce(k=150)
    brute_force_layer.index_from_dataset(
      tf.data.Dataset.zip((products.batch(100), products.batch(100).map(product_model)))
    )

    cached_test = train.batch(1)

    test_sample = cached_test.skip(i).take(1)
    test_sample_map = test_sample.map(
            lambda features: tf.concat([model.user_model(features["user_id"]), model.user_model1(features["Area_Code"]),model.user_model2(features["SalesDocumentType"]),model.user_model3(features["Customer_Type"]), model.user_model4(features["city_name"]), model.user_model5(features["OfficeBk"]), model.user_model6(features["ClassBk"])], axis=1)
        )

    test_sample_map_arr = []
    for item in test_sample_map.take(1).as_numpy_iterator():
        test_sample_map_arr.append(item[0])
    test_sample_map_arr = np.array(test_sample_map_arr)

    afinity_scores, a = brute_force_layer(test_sample_map_arr)

    for item in test_sample.as_numpy_iterator():
        print(f"Recommendations for user {item['user_id']} using BruteForce: {i}")
        # ppp = 1

    l1.append(int(item['user_id']))
    # Get recommendations.
    # _, titles = index(tf.constant([i]))
    z=list(a[0, :150].numpy())
    for j in z:
        l1.append(int(j))
        
    l.append(l1)

2022-09-27 08:51:15.023866: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


Recommendations for user [b'222015516'] using BruteForce: 0


2022-09-27 08:51:15.265219: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.
2022-09-27 08:51:15.725956: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


Recommendations for user [b'305004775'] using BruteForce: 1
Recommendations for user [b'245012438'] using BruteForce: 2
Recommendations for user [b'242081629'] using BruteForce: 3
Recommendations for user [b'243092006'] using BruteForce: 4
Recommendations for user [b'611502242'] using BruteForce: 5
Recommendations for user [b'273084657'] using BruteForce: 6
Recommendations for user [b'230443873'] using BruteForce: 7
Recommendations for user [b'451040151'] using BruteForce: 8
Recommendations for user [b'319000105'] using BruteForce: 9
Recommendations for user [b'422053454'] using BruteForce: 10
Recommendations for user [b'451038674'] using BruteForce: 11
Recommendations for user [b'221015072'] using BruteForce: 12
Recommendations for user [b'221015456'] using BruteForce: 13
Recommendations for user [b'306000354'] using BruteForce: 14
Recommendations for user [b'316007444'] using BruteForce: 15
Recommendations for user [b'320000188'] using BruteForce: 16
Recommendations for user [b'25400

In [154]:
len(l)

10000

In [155]:
dd1=pd.DataFrame(l)

In [156]:
dd1

0     1     2     3     4     5     6     7     8     9    ...  \
0     222015516  3013  3014   374   366  1912  2842  2010  1910  1911  ...   
1     305004775  1758   230   827  2869  1756  2862   227   137  3011  ...   
2     245012438  2852  3120  2855  2850  1901  1902  1900   228  1903  ...   
3     242081629  2884  2882   827  1649  1647  1645  1678  1648  2880  ...   
4     243092006  1946  1466  1945  1458  1944  1854  1947  1448  1434  ...   
...         ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
9995  319000131  3076   312  1070   283  1071  2201  1098   282  1063  ...   
9996  247092427   664  2993  1437   642  2994  1439  1591  2896   651  ...   
9997  230444021  2911  2908  1649  1646  1648  1645  2898  2910  1912  ...   
9998  254007929  2613  2610  2629  2869  2868  3038   221  2861   790  ...   
9999  608011255  1097  1062  2631  2630   221  2613  1063  2610  1619  ...   

       141   142   143   144   145   146   147   148   149   150  
0     1585  1280   207  1094  2520  2903  2509  2521   400  2888  
1     3030  1760  1588  2629  3076   559   927  1596  3120  2518  
2     1628   331  1597   788  1473  1914  3034  2021   385   224  
3     2469  2824  1576   221  1897  2010   643  2784  1854  3030  
4     1644  2992  1470  1858   276  1576  1954   400  1761  1684  
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
9995  1763  2842  1523   788  2241  1753  1808  2855   366  1806  
9996  1579   206  1764  2035  1675  1281   501   508  3079   366  
9997  1844  1773  3077  1902  1628  2913  1940  3120  2945   664  
9998  3120   927  1571   385  1752  1585   230  1675  1523  1775  
9999   654  1464  1849   134   783  2323   788  1096   649   224  

[10000 rows x 151 columns]

In [157]:
dd1.to_csv('part2.csv')

In [158]:
df5=df.iloc[20000:30000,:]

In [159]:
df5=df5.reset_index()

In [160]:
df5=df5.iloc[:,1:]

In [161]:
df5

CustomerBk CustomerTypeBk AreaBk CityTitle OfficeBk DistPathCode  \
0     611502524             37      0     تهران      156            1   
1     611502527             37      0     تهران      156            2   
2     611502529             37      0     تهران      156            1   
3     611502531             37      0     تهران      959            1   
4     611502532             37      0     تهران      156            1   
...         ...            ...    ...       ...      ...          ...   
9995  950442606             37      0    باسمنج      950            0   
9996  950442607             37      0     تبريز      950            0   
9997  950442609             42      0     تبريز      950            0   
9998  950442615             37      0     تبريز      950            0   
9999  950442619             26      0     تبريز      950            0   

     LastCustomerClassBk  
0                    100  
1                     50  
2                     50  
3                    100  
4                    100  
...                  ...  
9995                 -10  
9996                 250  
9997                 -10  
9998                 300  
9999                 300  

[10000 rows x 7 columns]

In [162]:
features = ['CustomerBk','AreaBk','DistPathCode','CustomerTypeBk','CityTitle','OfficeBk','LastCustomerClassBk'] 
dataset = (
    tf.data.Dataset.from_tensor_slices(
        (
            tf.cast(df5[features].values, tf.string)
            
        )
    )
)

In [163]:
ratings = (dataset
           .map(lambda rating: {'user_id': rating[0],'Area_Code':rating[1],'SalesDocumentType':rating[2],'Customer_Type':rating[3],'city_name':rating[4],'OfficeBk':rating[5],'ClassBk':rating[6]})
           .cache(tempfile.NamedTemporaryFile().name)
)

In [164]:
tf.random.set_seed(42)
shuffled = ratings.shuffle(10000 , seed=42, reshuffle_each_iteration=False)

train = shuffled.take(10000)


In [165]:
l=[]
for i in range(10000):
    l1=[]
    # index = tfrs.layers.factorized_top_k.BruteForce(model.user_model,100)
    # # recommends movies out of the entire movies dataset.
    # index.index_from_dataset(
    #   tf.data.Dataset.zip((products.batch(100), products.batch(100).map(product_model)))
    # )
    brute_force_layer = tfrs.layers.factorized_top_k.BruteForce(k=150)
    brute_force_layer.index_from_dataset(
      tf.data.Dataset.zip((products.batch(100), products.batch(100).map(product_model)))
    )

    cached_test = train.batch(1)

    test_sample = cached_test.skip(i).take(1)
    test_sample_map = test_sample.map(
            lambda features: tf.concat([model.user_model(features["user_id"]), model.user_model1(features["Area_Code"]),model.user_model2(features["SalesDocumentType"]),model.user_model3(features["Customer_Type"]), model.user_model4(features["city_name"]), model.user_model5(features["OfficeBk"]), model.user_model6(features["ClassBk"])], axis=1)
        )

    test_sample_map_arr = []
    for item in test_sample_map.take(1).as_numpy_iterator():
        test_sample_map_arr.append(item[0])
    test_sample_map_arr = np.array(test_sample_map_arr)

    afinity_scores, a = brute_force_layer(test_sample_map_arr)

    for item in test_sample.as_numpy_iterator():
        print(f"Recommendations for user {item['user_id']} using BruteForce: {i}")
        # ppp = 1

    l1.append(int(item['user_id']))
    # Get recommendations.
    # _, titles = index(tf.constant([i]))
    z=list(a[0, :150].numpy())
    for j in z:
        l1.append(int(j))
        
    l.append(l1)

2022-09-27 10:15:05.810625: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


Recommendations for user [b'613013700'] using BruteForce: 0


2022-09-27 10:15:06.055158: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.
2022-09-27 10:15:06.485967: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


Recommendations for user [b'625004015'] using BruteForce: 1
Recommendations for user [b'620034328'] using BruteForce: 2
Recommendations for user [b'619007115'] using BruteForce: 3
Recommendations for user [b'619502446'] using BruteForce: 4
Recommendations for user [b'950442358'] using BruteForce: 5
Recommendations for user [b'624004159'] using BruteForce: 6
Recommendations for user [b'615000015'] using BruteForce: 7
Recommendations for user [b'839442610'] using BruteForce: 8
Recommendations for user [b'635501963'] using BruteForce: 9
Recommendations for user [b'814030804'] using BruteForce: 10
Recommendations for user [b'825502411'] using BruteForce: 11
Recommendations for user [b'612037465'] using BruteForce: 12
Recommendations for user [b'612040565'] using BruteForce: 13
Recommendations for user [b'625014524'] using BruteForce: 14
Recommendations for user [b'633000401'] using BruteForce: 15
Recommendations for user [b'638502529'] using BruteForce: 16
Recommendations for user [b'62210

In [166]:
len(l)

10000

In [167]:
dd1=pd.DataFrame(l)

In [168]:
dd1

0     1     2     3     4     5     6     7     8     9    ...  \
0     613013700   908  1775  1773  2761  1760  1771  1774  1772   331  ...   
1     625004015  1858  1857  1854  1894  1899  1859  1856  1941  2972  ...   
2     620034328  1949  1661   707   732  2977  1603   457   722  1498  ...   
3     619007115  1571  1576   360  2363  2111   325   206  2351   370  ...   
4     619502446  1612  1609  1661  1582  1949  1664  1533  2702   224  ...   
...         ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
9995  635502330  2868  2862  2861  1606  2869  1775  2866  2883  2867  ...   
9996  620100608  1664  1661  2977  2978  1608  1609  1484  1644  1899  ...   
9997  616033083  1456   291  2911  2914  2867  1439  1435   279   296  ...   
9998  622101162  2358  2114  1685  2865  1933   650   218   207  2864  ...   
9999  943561044  2613   221  2623  2629  2610  2630  1606  2516  2609  ...   

       141   142   143   144   145   146   147   148   149   150  
0      238  2021  3046  3032  1099  2865  2913  3038  2883  2862  
1     1282  2781  1947   367   643  3079   657  1053  2030  1952  
2      207   908  1622   239  1904  1687  2781  1478   139  1946  
3      683   657  2518  1586   927   650  1288  3013   705  1899  
4     1771  1952   474  2255  2112   147  2241  1448  1435  3000  
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
9995  2945   797   504   655  1765  1093  1902   329   508   753  
9996  1613   201  1910   825  1467   374  1498   375  1439  1651  
9997  2903  1521  1844  2915  1578   235  2509  1946  1282  2262  
9998  3003   201  1854  1585  2841   365  1522  2844  1605  1614  
9999   657  2469  1618  1463  2881   147   230   366  1098   558  

[10000 rows x 151 columns]

In [169]:
dd1.to_csv('part3.csv')

In [199]:
df5=df.iloc[30000:40000,:]

In [200]:
df5=df5.reset_index()

In [201]:
df5=df5.iloc[:,1:]

In [202]:
df5

CustomerBk CustomerTypeBk AreaBk  CityTitle OfficeBk DistPathCode  \
0     950442620             37      0      تبريز      950            0   
1     950442621             37      0      تبريز      950            0   
2     950442626             37      0      تبريز      950            0   
3     950442628             37      0      تبريز      950            0   
4     950442630             45      0      تبريز      133            0   
...         ...            ...    ...        ...      ...          ...   
9995  975013560             37      0  شاهين شهر      975            0   
9996  975013561             37      0  شاهين شهر      975            0   
9997  975013564             37      0     بادرود      975            0   
9998  975013565             37      0      داران      975            0   
9999  975013568             37      0  فريدونشهر      975            0   

     LastCustomerClassBk  
0                    -10  
1                    300  
2                    300  
3                    -10  
4                    300  
...                  ...  
9995                 300  
9996                 300  
9997                 300  
9998                 -10  
9999                 -10  

[10000 rows x 7 columns]

In [203]:
features = ['CustomerBk','AreaBk','DistPathCode','CustomerTypeBk','CityTitle','OfficeBk','LastCustomerClassBk'] 
dataset = (
    tf.data.Dataset.from_tensor_slices(
        (
            tf.cast(df5[features].values, tf.string)
            
        )
    )
)

In [204]:
ratings = (dataset
           .map(lambda rating: {'user_id': rating[0],'Area_Code':rating[1],'SalesDocumentType':rating[2],'Customer_Type':rating[3],'city_name':rating[4],'OfficeBk':rating[5],'ClassBk':rating[6]})
           .cache(tempfile.NamedTemporaryFile().name)
)

In [205]:
tf.random.set_seed(42)
shuffled = ratings.shuffle(10000 , seed=42, reshuffle_each_iteration=False)

train = shuffled.take(10000)


In [206]:
l=[]
for i in range(10000):
    l1=[]
    # index = tfrs.layers.factorized_top_k.BruteForce(model.user_model,100)
    # # recommends movies out of the entire movies dataset.
    # index.index_from_dataset(
    #   tf.data.Dataset.zip((products.batch(100), products.batch(100).map(product_model)))
    # )
    brute_force_layer = tfrs.layers.factorized_top_k.BruteForce(k=150)
    brute_force_layer.index_from_dataset(
      tf.data.Dataset.zip((products.batch(100), products.batch(100).map(product_model)))
    )

    cached_test = train.batch(1)

    test_sample = cached_test.skip(i).take(1)
    test_sample_map = test_sample.map(
            lambda features: tf.concat([model.user_model(features["user_id"]), model.user_model1(features["Area_Code"]),model.user_model2(features["SalesDocumentType"]),model.user_model3(features["Customer_Type"]), model.user_model4(features["city_name"]), model.user_model5(features["OfficeBk"]), model.user_model6(features["ClassBk"])], axis=1)
        )

    test_sample_map_arr = []
    for item in test_sample_map.take(1).as_numpy_iterator():
        test_sample_map_arr.append(item[0])
    test_sample_map_arr = np.array(test_sample_map_arr)

    afinity_scores, a = brute_force_layer(test_sample_map_arr)

    for item in test_sample.as_numpy_iterator():
        print(f"Recommendations for user {item['user_id']} using BruteForce: {i}")
        # ppp = 1

    l1.append(int(item['user_id']))
    # Get recommendations.
    # _, titles = index(tf.constant([i]))
    z=list(a[0, :150].numpy())
    for j in z:
        l1.append(int(j))
        
    l.append(l1)

2022-09-28 10:00:26.453871: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


Recommendations for user [b'950443724'] using BruteForce: 0


2022-09-28 10:00:26.684380: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.
2022-09-28 10:00:27.128166: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


Recommendations for user [b'959503582'] using BruteForce: 1
Recommendations for user [b'951062465'] using BruteForce: 2
Recommendations for user [b'951061477'] using BruteForce: 3
Recommendations for user [b'951062030'] using BruteForce: 4
Recommendations for user [b'973443467'] using BruteForce: 5
Recommendations for user [b'957561987'] using BruteForce: 6
Recommendations for user [b'950444105'] using BruteForce: 7
Recommendations for user [b'972442817'] using BruteForce: 8
Recommendations for user [b'965442605'] using BruteForce: 9
Recommendations for user [b'971017013'] using BruteForce: 10
Recommendations for user [b'972442572'] using BruteForce: 11
Recommendations for user [b'950443155'] using BruteForce: 12
Recommendations for user [b'950443322'] using BruteForce: 13
Recommendations for user [b'959503670'] using BruteForce: 14
Recommendations for user [b'963443712'] using BruteForce: 15
Recommendations for user [b'965443274'] using BruteForce: 16
Recommendations for user [b'95656

In [207]:
len(l)

10000

In [208]:
dd1=pd.DataFrame(l)

In [209]:
dd1

0     1     2     3     4     5     6     7     8     9    ...  \
0     950443724  1899  1844  1911  1691  1910  1840  1912  1841  1858  ...   
1     959503582  2905  2903  2930  2897  2904  2899  2898  2910  2906  ...   
2     951062465   805  1098   806  1097  1651  2784  1099   221  3032  ...   
3     951061477   276   278   221   284  2610  2609   230   282  2211  ...   
4     951062030   559  1651   508   805  2211  3078   589  2011   558  ...   
...         ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
9995  965442637   221  1618  2610   736  1274  2784  3032  1461  2869  ...   
9996  952560702   282   276   239   232   278   275   238   277   235  ...   
9997  950444294  2520  2521  2522  1053  1055  1054  2518  2469  1059  ...   
9998  956561102  1904  1913  1914  1903  1901  1902  1900  1912  1910  ...   
9999  972443621  1912  1911  1910  1914  1913   460  1676  1675  2978  ...   

       141   142   143   144   145   146   147   148   149   150  
0     3030  1612  3079  2892  2324  2518   460  1676   367  1094  
1      649   558  2701   400   717   238  1761  2363  2623  2751  
2     1465   809   366  1806  2972   235   296   505  2853   275  
3     2752  2904  2466  3034   808  1809   715  1648   505  2896  
4     2521  2245  1895   717  2114  3015  2854  2468  2031  1099  
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
9995  2111  1542   282  1288   807  1804   218  1071   292  2864  
9996  1682  1802   732  1901  1900  2629   790   722   294   367  
9997  2833  1913  2895  1096  2897  2245   379  2909   420  1664  
9998   742  3078  1454  2889   360   279  1448  2241  1576   289  
9999  1408  1685   785  2971  2999  3077  2518  1086  1071  1587  

[10000 rows x 151 columns]

In [210]:
dd1.to_csv('part4.csv')

In [ ]:
##اجرای پارت آخر دیتا 40000-...

In [179]:
df5=df.iloc[40000:,:]

In [180]:
df5=df5.reset_index()

In [181]:
df5=df5.iloc[:,1:]

In [182]:
df5

CustomerBk CustomerTypeBk AreaBk  CityTitle OfficeBk DistPathCode  \
0      975013571             37      0   نجف آباد      975            0   
1      975013572             37      0   نجف آباد      975            0   
2      975013573             37      0  امير آباد      975            0   
3      975013576             37      0    خوانسار      975            0   
4      975013579             37      0    خوانسار      975            0   
...          ...            ...    ...        ...      ...          ...   
16175  992084763             37      0        رشت      273            0   
16176  998442479             26      0      اهواز      998            0   
16177  998442480             22      0      اهواز      998            0   
16178  998442482             22      0      اهواز      998            0   
16179  999562001              9      0      تهران      999            0   

      LastCustomerClassBk  
0                     300  
1                     300  
2                     300  
3                     300  
4                     300  
...                   ...  
16175                 -10  
16176                 -10  
16177                 -10  
16178                 -10  
16179                 -10  

[16180 rows x 7 columns]

In [183]:
ledf5 = len(df5)

In [184]:
features = ['CustomerBk','AreaBk','DistPathCode','CustomerTypeBk','CityTitle','OfficeBk','LastCustomerClassBk'] 
dataset = (
    tf.data.Dataset.from_tensor_slices(
        (
            tf.cast(df5[features].values, tf.string)
            
        )
    )
)

In [185]:
ratings = (dataset
           .map(lambda rating: {'user_id': rating[0],'Area_Code':rating[1],'SalesDocumentType':rating[2],'Customer_Type':rating[3],'city_name':rating[4],'OfficeBk':rating[5],'ClassBk':rating[6]})
           .cache(tempfile.NamedTemporaryFile().name)
)

In [186]:
tf.random.set_seed(42)
shuffled = ratings.shuffle(ledf5 , seed=42, reshuffle_each_iteration=False)

train = shuffled.take(ledf5)


In [187]:
l=[]
for i in range(ledf5):
    l1=[]
    # index = tfrs.layers.factorized_top_k.BruteForce(model.user_model,100)
    # # recommends movies out of the entire movies dataset.
    # index.index_from_dataset(
    #   tf.data.Dataset.zip((products.batch(100), products.batch(100).map(product_model)))
    # )
    brute_force_layer = tfrs.layers.factorized_top_k.BruteForce(k=150)
    brute_force_layer.index_from_dataset(
      tf.data.Dataset.zip((products.batch(100), products.batch(100).map(product_model)))
    )

    cached_test = train.batch(1)

    test_sample = cached_test.skip(i).take(1)
    test_sample_map = test_sample.map(
            lambda features: tf.concat([model.user_model(features["user_id"]), model.user_model1(features["Area_Code"]),model.user_model2(features["SalesDocumentType"]),model.user_model3(features["Customer_Type"]), model.user_model4(features["city_name"]), model.user_model5(features["OfficeBk"]), model.user_model6(features["ClassBk"])], axis=1)
        )

    test_sample_map_arr = []
    for item in test_sample_map.take(1).as_numpy_iterator():
        test_sample_map_arr.append(item[0])
    test_sample_map_arr = np.array(test_sample_map_arr)

    afinity_scores, a = brute_force_layer(test_sample_map_arr)

    for item in test_sample.as_numpy_iterator():
        print(f"Recommendations for user {item['user_id']} using BruteForce: {i}")
        # ppp = 1

    l1.append(int(item['user_id']))
    # Get recommendations.
    # _, titles = index(tf.constant([i]))
    z=list(a[0, :150].numpy())
    for j in z:
        l1.append(int(j))
        
    l.append(l1)

2022-09-28 06:10:50.260205: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


Recommendations for user [b'147561292'] using BruteForce: 0


2022-09-28 06:10:50.587089: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.
2022-09-28 06:10:51.275384: W tensorflow/core/kernels/data/cache_dataset_ops.cc:233] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


Recommendations for user [b'319000244'] using BruteForce: 1
Recommendations for user [b'999561264'] using BruteForce: 2
Recommendations for user [b'972443558'] using BruteForce: 3
Recommendations for user [b'972443853'] using BruteForce: 4
Recommendations for user [b'999561777'] using BruteForce: 5
Recommendations for user [b'623501845'] using BruteForce: 6
Recommendations for user [b'992082829'] using BruteForce: 7
Recommendations for user [b'982012379'] using BruteForce: 8
Recommendations for user [b'825502573'] using BruteForce: 9
Recommendations for user [b'957563281'] using BruteForce: 10
Recommendations for user [b'621501177'] using BruteForce: 11
Recommendations for user [b'982012765'] using BruteForce: 12
Recommendations for user [b'983012478'] using BruteForce: 13
Recommendations for user [b'818007407'] using BruteForce: 14
Recommendations for user [b'992083577'] using BruteForce: 15
Recommendations for user [b'146562221'] using BruteForce: 16
Recommendations for user [b'98201

In [188]:
len(l)

16180

In [189]:
dd1=pd.DataFrame(l)

In [190]:
dd1

0     1     2     3     4     5     6     7     8     9    ...  \
0      147561292  2868   279  2351  2363  2101   218   207  2761  2111  ...   
1      319000244  3076  3011  1476   589  1752  1754  1282   230  2201  ...   
2      999561264  2018   206  2888   825  2112  2111  2363  2364   201  ...   
3      972443558  1676  2865  2868  1282  1568  1675  1476  2019   207  ...   
4      972443853  1676  2865  2868  1282  1568  1675  1476  2019   207  ...   
...          ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
16175  951062459   279   805   589  2111   714   508  3030   591   708  ...   
16176  219030282   785  3032   407   508  1651  3078  3030  3033   360  ...   
16177  316007044  1758  1754  3011  1752   230  1753  3079  2125   228  ...   
16178  614000034   279  2865  2761  2613  2868   907   908   927   504  ...   
16179  994013600  2864   589  1911  1910  1912   400  1760  1761  3033  ...   

        141   142   143   144   145   146   147   148   149   150  
0       134  2014   761  2467  2018   806  2016   278  2324   753  
1       496   374  1576  1070  2841   667  1757  2040  2701  1649  
2      2840   229  2005  1523  1588  2022  3046   291   649  1859  
3      1435  1583  2999  1449  1094   420  2101  1524   201   232  
4      1435  1583  2999  1449  1094   420  2101  1524   201   232  
...     ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
16175  2855  1770   228  1094   642  1586  1598   651  2035  2510  
16176  2854   294   504   789  2211   655  1596  2855   292   235  
16177  1646  1524  1590  2323  2017  1094  1086  3033   201  1467  
16178  3003  2850  1614  1805  1899   275  2521  1857  1803  2010  
16179  2891   279  1770  1608  2971  1771  1054  1281  3116   367  

[16180 rows x 151 columns]

In [191]:
dd1.to_csv('part5.csv')

In [192]:
dff1 = pd.read_csv('part1.csv')

In [193]:
dff2 = pd.read_csv('part2.csv')

In [194]:
dff3 = pd.read_csv('part3.csv')

In [211]:
dff4 = pd.read_csv('part4.csv')

In [196]:
dff5 = pd.read_csv('part5.csv')

In [212]:
dff5=pd.concat([dff1, dff2,dff3,dff4,dff5])
dff5=dff5.reset_index()
dff5=dff5.iloc[:,1:]


In [213]:
dff5

Unnamed: 0          0     1     2     3     4     5     6     7     8  \
0               0  134442360  2211   232  2364  2323   239  2112   238   235   
1               1  155561306  2018  2041  2509  1952   819  2761   508   501   
2               2  146561260  1053  2761  1847  1055   279  2865  3032   457   
3               3  144442815  1093  2613   221  1099  1070  1094   805   788   
4               4  144443404  2613   221  2610  2629   277   275   276   232   
...           ...        ...   ...   ...   ...   ...   ...   ...   ...   ...   
56175       16175  951062459   279   805   589  2111   714   508  3030   591   
56176       16176  219030282   785  3032   407   508  1651  3078  3030  3033   
56177       16177  316007044  1758  1754  3011  1752   230  1753  3079  2125   
56178       16178  614000034   279  2865  2761  2613  2868   907   908   927   
56179       16179  994013600  2864   589  1911  1910  1912   400  1760  1761   

       ...   141   142   143   144   145   146   147   148   149   150  
0      ...  1664  3121   460   291  1685  1062  1532  1648   657  2018  
1      ...  3121   827   496  1449   235   238   137   407  1618  2245  
2      ...  1474  2509  1763  2011  1608   703  3014   325   650  2905  
3      ...  1930  1583   230  1449   370  2905  1077   808   736  1438  
4      ...  2041   420   377   137  1765   375   457   383  2885  3010  
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
56175  ...  2855  1770   228  1094   642  1586  1598   651  2035  2510  
56176  ...  2854   294   504   789  2211   655  1596  2855   292   235  
56177  ...  1646  1524  1590  2323  2017  1094  1086  3033   201  1467  
56178  ...  3003  2850  1614  1805  1899   275  2521  1857  1803  2010  
56179  ...  2891   279  1770  1608  2971  1771  1054  1281  3116   367  

[56180 rows x 152 columns]

In [214]:
dff5=dff5.iloc[:,1:]

In [215]:
dff5

0     1     2     3     4     5     6     7     8     9  ...  \
0      134442360  2211   232  2364  2323   239  2112   238   235   277  ...   
1      155561306  2018  2041  2509  1952   819  2761   508   501  1661  ...   
2      146561260  1053  2761  1847  1055   279  2865  3032   457  2363  ...   
3      144442815  1093  2613   221  1099  1070  1094   805   788   371  ...   
4      144443404  2613   221  2610  2629   277   275   276   232   235  ...   
...          ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
56175  951062459   279   805   589  2111   714   508  3030   591   708  ...   
56176  219030282   785  3032   407   508  1651  3078  3030  3033   360  ...   
56177  316007044  1758  1754  3011  1752   230  1753  3079  2125   228  ...   
56178  614000034   279  2865  2761  2613  2868   907   908   927   504  ...   
56179  994013600  2864   589  1911  1910  1912   400  1760  1761  3033  ...   

        141   142   143   144   145   146   147   148   149   150  
0      1664  3121   460   291  1685  1062  1532  1648   657  2018  
1      3121   827   496  1449   235   238   137   407  1618  2245  
2      1474  2509  1763  2011  1608   703  3014   325   650  2905  
3      1930  1583   230  1449   370  2905  1077   808   736  1438  
4      2041   420   377   137  1765   375   457   383  2885  3010  
...     ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
56175  2855  1770   228  1094   642  1586  1598   651  2035  2510  
56176  2854   294   504   789  2211   655  1596  2855   292   235  
56177  1646  1524  1590  2323  2017  1094  1086  3033   201  1467  
56178  3003  2850  1614  1805  1899   275  2521  1857  1803  2010  
56179  2891   279  1770  1608  2971  1771  1054  1281  3116   367  

[56180 rows x 151 columns]

In [216]:
dff5.to_csv('kalan_final.csv')

In [ ]:
#!python3 costomer-interval.py